In [3]:
import numpy as np
from Bio.PDB import *

In [101]:
import os

In [242]:
import time

In [246]:
import subprocess

In [209]:
def match_score(a1,a2,l_min):
    """
    Calculate aligned score
    """
    d0 = 1.24 * (l_min-15)**(1/3) - 1.8
    
    return 1/( 1 + ((a1-a2)**2) / (d0**2) )

def matrix_update(seq0,seq1):
    
    """
    Calculate DP matrix for needleman wunsch, gap penalty 0.6
    """
    
    pdb0_len = len(seq0)
    pdb1_len = len(seq1)
    lmin = min(pdb0_len,pdb1_len)
    dp_matrix = np.zeros([pdb0_len+1,pdb1_len+1,2])
    for i in range(1,pdb0_len+1):
        dp_matrix[i,0,0] = -0.6*i
        dp_matrix[i,0,1] = 0
    for j in range(1,pdb1_len+1):
        dp_matrix[0,j,0] = -0.6*j
        dp_matrix[0,j,1] = 1
    for i in range(1,dp_matrix.shape[0]):
        for j in range(1,dp_matrix.shape[1]):
            dp_matrix[i,j,0] = np.max([dp_matrix[i-1,j,0]-0.6, dp_matrix[i,j-1,0]-0.6, dp_matrix[i-1,j-1,0]+match_score(seq0[i-1],seq1[j-1],lmin)])
            dp_matrix[i,j,1] = np.argmax([dp_matrix[i-1,j,0]-0.6, dp_matrix[i,j-1,0]-0.6, dp_matrix[i-1,j-1,0]+match_score(seq0[i-1],seq1[j-1],lmin)])
    return dp_matrix

def back_tracing(seq0,seq1,mtx):
    """
    Tracing of the DP matrix
    """
    
    seq0_m = []
    seq1_m = []
    i = mtx.shape[0] -1
    j = mtx.shape[1] - 1
    while(i !=0 and j != 0):
        if mtx[i,j,1] == 0:
            i -= 1
            continue
        elif mtx[i,j,1] == 1:
            j -= 1
            continue
        else:
            seq0_m.append(seq0[i-1])
            seq1_m.append(seq1[j-1])
            i -= 1
            j -= 1
    return seq0_m[::-1],seq1_m[::-1]

In [285]:
def TM_align_execute(pdb_0_path,pdb_1_path):

    """
    Ran TM align from python
    """
    
    a =subprocess.run(["/home/chingyuenliu/TTIC31160_bioinfo/hw4/TM_align/TMalign", pdb_0_path, pdb_1_path], \
                      capture_output=True)
    output  = a.stdout

    output_list = output.split(b'\n')
    
    value_tm_np = np.zeros(5)

    l_tar = 0
    for i in range(len(output_list)):
        if output_list[i].startswith(b'Length of Chain_1'):
            l_tar = int(output_list[i].split()[-2])
        if output_list[i].startswith(b'Aligned'):
            seg_list = output_list[i].split()
            value_tm_np[1] = int(seg_list[2].strip(b','))
            value_tm_np[0] = float(seg_list[4].strip(b','))
            value_tm_np[3] = float(output_list[i+1].split()[1])
        if output_list[i].startswith(b'Total CPU time'):
            value_tm_np[-1] = float(output_list[i].split()[-2])
    value_tm_np[2] = value_tm_np[1]/l_tar
    
    return value_tm_np

In [241]:
def TM_score(seq0_aln,seq1_aln,l_target):
    """
    Calculate TM score
    """
    tm_score_list = np.zeros(len(seq0_aln))
    for i in range(tm_score_list.shape[0]):
        tm_score_list[i] = match_score(seq0_aln[i],seq1_aln[i],l_target)
    return (tm_score_list.sum())/l_target

In [69]:
one2all ={'A': ('A', 'ALA', 'alanine'),
              'R': ('R', 'ARG', 'arginine'),
              'N': ('N', 'ASN', 'asparagine'),
              'D': ('D', 'ASP', 'aspartic acid'),
              'C': ('C', 'CYS', 'cysteine'),
              'Q': ('Q', 'GLN', 'glutamine'),
              'E': ('E', 'GLU', 'glutamic acid'),
              'G': ('G', 'GLY', 'glycine'),
              'H': ('H', 'HIS', 'histidine'),
              'I': ('I', 'ILE', 'isoleucine'),
              'L': ('L', 'LEU', 'leucine'),
              'K': ('K', 'LYS', 'lysine'),
              'M': ('M', 'MET', 'methionine'),
              'F': ('F', 'PHE', 'phenylalanine'),
              'P': ('P', 'PRO', 'proline'),
              'S': ('S', 'SER', 'serine'),
              'T': ('T', 'THR', 'threonine'),
              'W': ('W', 'TRP', 'tryptophan'),
              'Y': ('Y', 'TYR', 'tyrosine'),
              'V': ('V', 'VAL', 'valine'),
              'X': ('X', 'GLX', 'glutaminx'),
              'Z': ('Z', 'GLI', 'glycine'),
              'J': ('J', 'NLE', 'norleucine'),
                'U': ('U', 'CYC', 'cysteinc')}

In [297]:
def pdb_check(root,file):
    
    """
    Check if pdb file is at directory
    """
    
    pdb_1, pdb_2 = file[:-6].split('-')
    if not os.path.exists(os.path.join(root,pdb_1)):
        print(os.path.join(root,pdb_1))
        return False
    if not os.path.exists(os.path.join(root,pdb_2)): 
        print(os.path.join(root,pdb_2))
        return False
    return True

In [287]:
super_directory ="/home/chingyuenliu/TTIC31160_bioinfo/hw2/Super_test"
twil_directory ="/home/chingyuenliu/TTIC31160_bioinfo/hw2/Twil_test"

In [308]:
"""
target_list: list that record all the targets
value_list: record all the output values based on the target list, [[]]
value_tm_list: same to value_list, but from preimplemented TM-align 
"""
target_list = []
value_list = []
value_tm_list = []
for root, dirs, files in os.walk(super_directory):
    for file in files:
        if file.endswith(".fasta") and file.startswith('d'):

            if not pdb_check(root,file):
                continue
            
            #pdb file name
            pdb_0, pdb_1 = file[:-6].split('-')
            #pdb file path
            pdb_0_path = os.path.join(root,pdb_0)
            pdb_1_path = os.path.join(root,pdb_1)
            # a matrix that record rmsd,aligned length, coverage, TM score and time for execution
            value_np = np.zeros(5)
            
            
            
            if not pdb_0 in target_list:
                target_list.append(pdb_0)
                value_list.append([])
                value_tm_list.append([])
            index = target_list.index(pdb_0)
            
            tic = time.perf_counter()
            #load PDB structure
            parser = PDBParser()
            structure_0 = parser.get_structure(pdb_0[:-4], pdb_0_path)
            structure_1 = parser.get_structure(pdb_1[:-4], pdb_1_path)
            
            #C-alpha sequence
            seq_0 = []
            seq_1 = []
            
            for a in Selection.unfold_entities(structure_0, "A"):
                if a.get_full_id()[3][0] != 'W' and a.get_name() == "CA" :
                    seq_0.append(a)
            for a in Selection.unfold_entities(structure_1, "A"):
                if a.get_full_id()[3][0] != 'W' and a.get_name() == "CA":
                    seq_1.append(a)

            #update alignment        
            flag1 = True
            align_len = 0
            counter =0
            while flag1:
                if counter > 5000:
                    break
                matrix = matrix_update(seq_0,seq_1)
                
                seq_0_m,seq_1_m = back_tracing(seq_0,seq_1,matrix)
                if len(seq_0_m) == align_len: 
                    flag1 = False
                    sup = Superimposer()
                    sup.set_atoms(seq_0_m, seq_1_m)
                    sup.apply(structure_1)
                    value_np[0] = sup.rms
                    value_np[1] = len(seq_0_m)
                    value_np[2] = len(seq_0_m)/len(seq_0)
                    value_np[3] = TM_score(seq_0_m,seq_1_m,len(seq_0))
                else:
                    align_len = len(seq_0_m)
                    sup = Superimposer()
                    sup.set_atoms(seq_0_m, seq_1_m)
                    sup.apply(structure_1)
                counter += 1
                
            toc = time.perf_counter()
            value_np[4] = toc-tic
            value_tm_list[index].append(TM_align_execute(pdb_0_path,pdb_1_path))
            
            value_list[index].append(value_np)
            
            
                
            

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

...

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

In [335]:
"""
Calculate the average of values
"""

value_matrix_list = []
value_tm_matrix_list =[]

for i in range(len(target_list)):
    value_matrix_list.append(np.array(value_list[i]))
    value_tm_matrix_list.append(np.array(value_tm_list[i]))

    
value_max_matrix_list = []
value_max_tm_matrix_list =[]

for i in range(len(value_matrix_list)):
    value_max_matrix_list.append(value_matrix_list[i][value_matrix_list[i][:,3].argmax(),:].reshape(1,-1))
    value_max_tm_matrix_list.append(value_tm_matrix_list[i][value_tm_matrix_list[i][:,3].argmax(),:].reshape(1,-1))

value_matrix = np.concatenate(value_matrix_list, axis=0).mean(axis= 0)
value_max_matrix = np.concatenate(value_max_matrix_list, axis=0).mean(axis= 0)
value_tm_matrix = np.concatenate(value_tm_matrix_list, axis=0).mean(axis= 0)
value_max_tm_matrix = np.concatenate(value_max_tm_matrix_list, axis=0).mean(axis= 0)

print(value_matrix) 
print(value_max_matrix)
print(value_tm_matrix)
print(value_max_tm_matrix)

[  5.03985101 139.01960784   0.9060316    0.61470443   2.53109187]
[  2.47563642 141.25925926   0.9460201    0.80774006   2.31328892]
[2.64679739e+00 1.33032680e+02 8.68990223e-01 7.01846209e-01
 3.50980392e-02]
[1.82888889e+00 1.38481481e+02 9.29951109e-01 8.25502593e-01
 3.29629630e-02]


In [336]:
"""
Check total num samples processed
"""
super_num_samples = 0
for i in value_matrix_list:
    super_num_samples += i.shape[0]
print(super_num_samples)

306


In [344]:
"""
Similar to superfamily dataset, but on twilight dataset
"""
target_list_twil = []
value_list_twil = []
value_tm_list_twil = []
for root, dirs, files in os.walk(twil_directory):
    for file in files:
        if file.endswith(".fasta") and file.startswith('d'):

            if not pdb_check(root,file):
                continue
            pdb_0, pdb_1 = file[:-6].split('-')

            pdb_0_path = os.path.join(root,pdb_0)
            pdb_1_path = os.path.join(root,pdb_1)
            value_np = np.zeros(5)
            
            
            
            if not pdb_0 in target_list_twil:
                target_list_twil.append(pdb_0)
                value_list_twil.append([])
                value_tm_list_twil.append([])
            index = target_list_twil.index(pdb_0)
            
            tic = time.perf_counter()
            
            parser = PDBParser()
            structure_0 = parser.get_structure(pdb_0[:-4], pdb_0_path)
            structure_1 = parser.get_structure(pdb_1[:-4], pdb_1_path)
            

            seq_0 = []
            seq_1 = []
            
            for a in Selection.unfold_entities(structure_0, "A"):
                if a.get_full_id()[3][0] != 'W' and a.get_name() == "CA" :
                    seq_0.append(a)
            for a in Selection.unfold_entities(structure_1, "A"):
                if a.get_full_id()[3][0] != 'W' and a.get_name() == "CA":
                    seq_1.append(a)

                    
            flag1 = True
            align_len = 0
            counter = 0
            while flag1:
                if counter >5000:
                    break
                matrix = matrix_update(seq_0,seq_1)
                
                seq_0_m,seq_1_m = back_tracing(seq_0,seq_1,matrix)
                if len(seq_0_m) == align_len: 
                    flag1 = False
                    sup = Superimposer()
                    sup.set_atoms(seq_0_m, seq_1_m)
                    sup.apply(structure_1)
                    value_np[0] = sup.rms
                    value_np[1] = len(seq_0_m)
                    value_np[2] = len(seq_0_m)/len(seq_0)
                    value_np[3] = TM_score(seq_0_m,seq_1_m,len(seq_0))
                else:
                    align_len = len(seq_0_m)
                    sup = Superimposer()
                    sup.set_atoms(seq_0_m, seq_1_m)
                    sup.apply(structure_1)
                counter += 1
            toc = time.perf_counter()
            value_np[4] = toc-tic
            value_tm_list_twil[index].append(TM_align_execute(pdb_0_path,pdb_1_path))
            
            value_list_twil[index].append(value_np)
            
            
                
            

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

...

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/chingyuenliu/miniconda3/lib/python3.7/site-packages/Bio/PDB/Atom.py:218: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  warnings.warn(ms

In [346]:
"""
Similar to superfamily dataset, but on twilight dataset
"""

value_matrix_list_twil = []
value_tm_matrix_list_twil =[]

for i in range(len(target_list_twil)):
    value_matrix_list_twil.append(np.array(value_list_twil[i]))
    value_tm_matrix_list_twil.append(np.array(value_tm_list_twil[i]))

    
value_max_matrix_list_twil = []
value_max_tm_matrix_list_twil =[]

for i in range(len(value_matrix_list_twil)):
    value_max_matrix_list_twil.append(value_matrix_list_twil[i][value_matrix_list_twil[i][:,3].argmax(),:].reshape(1,-1))
    value_max_tm_matrix_list_twil.append(value_tm_matrix_list_twil[i][value_tm_matrix_list_twil[i][:,3].argmax(),:].reshape(1,-1))

value_matrix_twil = np.concatenate(value_matrix_list_twil, axis=0).mean(axis= 0)
value_max_matrix_twil = np.concatenate(value_max_matrix_list_twil, axis=0).mean(axis= 0)
value_tm_matrix_twil = np.concatenate(value_tm_matrix_list_twil, axis=0).mean(axis= 0)
value_max_tm_matrix_twil = np.concatenate(value_max_tm_matrix_list_twil, axis=0).mean(axis= 0)

print(value_matrix_twil) 
print(value_max_matrix_twil)
print(value_tm_matrix_twil)
print(value_max_tm_matrix_twil)

[ 8.16182849 83.14903846  0.89064464  0.32381943 10.85819172]
[ 4.63869019 91.11111111  0.89512499  0.53022375  1.33915747]
[2.76975962e+00 7.00384615e+01 7.52700490e-01 5.37156587e-01
 1.61538462e-02]
[2.36592593e+00 8.46666667e+01 8.33516375e-01 6.58385556e-01
 1.74074074e-02]


In [343]:
"""
Similar to superfamily dataset, but on twilight dataset
"""
twil_num_samples = 0
for i in value_matrix_list_twil:
    twil_num_samples += i.shape[0]
print(twil_num_samples)

208
